## Import library

In [1]:
# importing required libraries
import os, sys
import sys
sys.path.insert(1, '/home/dtd/Documents/interpretable_machine_learning/Source Code/my_work/lib')
sys.path.insert(1, '/home/dtd/Documents/interpretable_machine_learning/Causal Inference/CEA')
import loader


import numpy as np
import pandas as pd
import logging
import dowhy.datasets
import dowhy
import propensity_score_estimator as pse
import incremental_ps_score_estimator as ipse
import math 
import timeit
from scipy.stats import sem

from dowhy import CausalModel
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
from sklearn.neighbors import NearestNeighbors
from sklearn.ensemble import RandomForestRegressor
from sklearn import metrics
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.metrics import explained_variance_score
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
from tqdm import tqdm
from sklearn.metrics import mean_squared_error
from math import sqrt
import evaluation as evl


ModuleNotFoundError: No module named 'loader'

## Do experiment on Dowhy package

In [2]:
PATH_TRAIN = "/home/dtd/Documents/interpretable_machine_learning/Source Code/data/ihdp_npci_1-1000.train.npz"
PATH_TEST = "/home/dtd/Documents/interpretable_machine_learning/Source Code/data/ihdp_npci_1-1000.test.npz"

In [9]:
import numpy as np
import pandas as pd
def load_data(path, i_exp):
    col =  ["t", "yf", "ycf", "mu0", "mu1" ]
    cov = ["x" + str(i) for i in range(1,26)]
    col = col + cov
    features = cov + ["t"] 
    D = np.load(path)
    df = pd.DataFrame(columns=col)

    for i in range(1,26):
        df['x' + str(i)]  = D['x'][:,i-1,i_exp-1]

    df['t']  = D['t'][:,i_exp-1:i_exp]
    df['yf'] = D['yf'][:,i_exp-1:i_exp]
    df['ycf'] = D['ycf'][:,i_exp-1:i_exp]
    df['mu0'] = D['mu0'][:,i_exp-1:i_exp]
    df['mu1'] = D['mu1'][:,i_exp-1:i_exp]
    return df

In [10]:
treatment = 't'
outcome = 'yf'
col =  ["t", "yf", "ycf", "mu0", "mu1" ]
cov = ["x" + str(i) for i in range(1,26)]
col = col + cov
features = cov + ["t"] 

In [11]:
df_train = load_data(PATH_TRAIN, 1)
df_test = load_data(PATH_TRAIN, 1)

In [22]:
df_train.shape

(672, 30)

In [17]:
D = np.load(PATH_TRAIN)
D['x'].shape

(672, 25, 1000)

In [6]:
linear_mae = []
ps_matching = []
ps_stratification = []
ps_weighting = []

for i in tqdm(range(1,1000)):    
    print(i)
    data = load_data(PATH_TRAIN, i)
    data[treatment] = [bool(x) for x in data[treatment]]

    true_effect = np.mean(data['mu1'] - data['mu0'])
    
    
    model=CausalModel(
            data = data,
            treatment='t',
            outcome='yf',
            common_causes=cov,
            proceed_when_unidentifiable=True
            )

    identified_estimand = model.identify_effect()

    estimate = model.estimate_effect(identified_estimand,
            method_name="backdoor.linear_regression", test_significance=True
    )
    
    mae = abs(estimate.value - true_effect)
    linear_mae.append(mae)
    
    estimate = model.estimate_effect(identified_estimand,
            method_name="backdoor.propensity_score_matching"
    )
    mae = abs(estimate.value - true_effect)
    ps_matching.append(mae)


    estimate = model.estimate_effect(identified_estimand,
            method_name="backdoor.propensity_score_stratification", method_params={'num_strata':50, 'clipping_threshold':5}
    )
    mae = abs(estimate.value - true_effect)
    ps_stratification.append(mae)


    estimate = model.estimate_effect(identified_estimand,
            method_name="backdoor.propensity_score_weighting"
    )
    mae = abs(estimate.value - true_effect)
    ps_weighting.append(mae)

  0%|          | 0/999 [00:00<?, ?it/s]

1


INFO:dowhy.causal_graph:If this is observed data (not from a randomized experiment), there might always be missing confounders. Adding a node named "Unobserved Confounders" to reflect this.
INFO:dowhy.causal_model:Model to find the causal effect of treatment ['t'] on outcome ['yf']
INFO:dowhy.causal_identifier:Common causes of treatment and outcome:['x24', 'x8', 'x19', 'x20', 'x9', 'x7', 'x3', 'x22', 'x14', 'x2', 'x1', 'x15', 'U', 'x4', 'x16', 'x21', 'x6', 'x12', 'x13', 'x10', 'x5', 'x18', 'x23', 'x25', 'x17', 'x11']
INFO:dowhy.causal_identifier:Continuing by ignoring these unobserved confounders because proceed_when_unidentifiable flag is True.
INFO:dowhy.causal_identifier:Instrumental variables for treatment and outcome:[]
INFO:dowhy.causal_estimator:INFO: Using Linear Regression Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
INFO:dowhy.causal_estimator:INFO: Using Propensity Score Matching Esti

                            OLS Regression Results                            
Dep. Variable:                     yf   R-squared:                       0.745
Model:                            OLS   Adj. R-squared:                  0.735
Method:                 Least Squares   F-statistic:                     72.57
Date:                Thu, 11 Jun 2020   Prob (F-statistic):          3.00e-172
Time:                        11:19:43   Log-Likelihood:                -1013.4
No. Observations:                 672   AIC:                             2081.
Df Residuals:                     645   BIC:                             2203.
Df Model:                          26                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const          2.1735      0.477      4.560      0.0

INFO:dowhy.causal_estimator:INFO: Using Propensity Score Stratification Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
/home/dtd/.conda/envs/phd_env/lib/python3.7/site-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
INFO:dowhy.causal_estimator:INFO: Using Propensity Score Weighting Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
/home/dtd/.conda/envs/phd_env/lib/python3.7/site-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
  0%|          | 1/999 [00:

...

INFO:dowhy.causal_estimator:INFO: Using Propensity Score Stratification Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
/home/dtd/.conda/envs/phd_env/lib/python3.7/site-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
INFO:dowhy.causal_estimator:INFO: Using Propensity Score Weighting Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
/home/dtd/.conda/envs/phd_env/lib/python3.7/site-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
100%|█████████▉| 998/999 [1

999


INFO:dowhy.causal_graph:If this is observed data (not from a randomized experiment), there might always be missing confounders. Adding a node named "Unobserved Confounders" to reflect this.
INFO:dowhy.causal_model:Model to find the causal effect of treatment ['t'] on outcome ['yf']
INFO:dowhy.causal_identifier:Common causes of treatment and outcome:['x24', 'x8', 'x19', 'x20', 'x9', 'x7', 'x3', 'x22', 'x14', 'x2', 'x1', 'x15', 'U', 'x4', 'x16', 'x21', 'x6', 'x12', 'x13', 'x10', 'x5', 'x18', 'x23', 'x25', 'x17', 'x11']
INFO:dowhy.causal_identifier:Continuing by ignoring these unobserved confounders because proceed_when_unidentifiable flag is True.
INFO:dowhy.causal_identifier:Instrumental variables for treatment and outcome:[]
INFO:dowhy.causal_estimator:INFO: Using Linear Regression Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
INFO:dowhy.causal_estimator:INFO: Using Propensity Score Matching Esti

                            OLS Regression Results                            
Dep. Variable:                     yf   R-squared:                       0.770
Model:                            OLS   Adj. R-squared:                  0.761
Method:                 Least Squares   F-statistic:                     83.10
Date:                Thu, 11 Jun 2020   Prob (F-statistic):          1.81e-186
Time:                        12:35:44   Log-Likelihood:                -934.38
No. Observations:                 672   AIC:                             1923.
Df Residuals:                     645   BIC:                             2045.
Df Model:                          26                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const          1.7956      0.414      4.341      0.0

INFO:dowhy.causal_estimator:INFO: Using Propensity Score Stratification Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
/home/dtd/.conda/envs/phd_env/lib/python3.7/site-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
INFO:dowhy.causal_estimator:INFO: Using Propensity Score Weighting Estimator
INFO:dowhy.causal_estimator:b: yf~t+x24+x8+x19+x20+x9+x7+x3+x22+x14+x2+x1+x15+x4+x16+x21+x6+x12+x13+x10+x5+x18+x23+x25+x17+x11
/home/dtd/.conda/envs/phd_env/lib/python3.7/site-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
100%|██████████| 999/999 [1

In [7]:
means, stds = np.mean(ps_weighting, axis=0), sem(ps_weighting, axis=0)
print('Weighting MAE: {:.3f}+-{:.3f}'.format(means, stds))

means, stds = np.mean(ps_stratification, axis=0), sem(ps_stratification, axis=0)
print('Stratification MAE: {:.3f}+-{:.3f}'.format(means, stds))

means, stds = np.mean(ps_matching, axis=0), sem(ps_matching, axis=0)
print('Matching MAE: {:.3f}+-{:.3f}'.format(means, stds))

means, stds = np.mean(linear_mae, axis=0), sem(linear_mae, axis=0)
print('Linear MAE: {:.3f}+-{:.3f}'.format(means, stds))

Weighting MAE: 1.661+-0.046
Stratification MAE: nan+-nan
Matching MAE: 0.202+-0.008
Linear MAE: 0.726+-0.038


## Do experiement on z-estimator

In [8]:
z_estimator_mae = []
delta_seq = np.linspace(0.5, 10, 50)
for i in tqdm(range(1,1000)):
    data = load_data(PATH_TRAIN, i)
    estimator = 'z_estimator'
    mae = ipse.experiment_z_estimator(data, treatment, cov, outcome, estimator, delta_seq)
    z_estimator_mae.append(mae)
    del data

 90%|█████████ | 45/50 [00:01<00:00, 45.22it/s]


100%|██████████| 50/50 [00:01<00:00, 44.80it/s]


  8%|▊         | 81/999 [12:26<2:21:39,  9.26s/it]


  0%|          | 0/50 [00:00<?, ?it/s]


  6%|▌         | 3/50 [00:00<00:01, 24.65it/s]


...

 90%|█████████ | 45/50 [00:00<00:00, 44.89it/s]


 90%|█████████ | 45/50 [00:01<00:00, 44.70it/s]


 88%|████████▊ | 44/50 [00:01<00:00, 43.22it/s]


100%|██████████| 50/50 [00:01<00:00, 44.70it/s]


100%|██████████| 999/999 [2:33:02<00:00,  9.19s/it]


In [9]:
means, stds = np.mean(z_estimator_mae, axis=0), sem(z_estimator_mae, axis=0)
print('Linear MAE: {:.3f}+-{:.3f}'.format(means, stds))

Linear MAE: 9.288+-0.401


In [10]:
means, stds = np.mean(ps_weighting, axis=0), sem(ps_weighting, axis=0)
print('Weighting MAE: {:.3f}+-{:.3f}'.format(means, stds))

# means, stds = np.mean(ps_stratification, axis=0), sem(ps_stratification, axis=0)
# print('Stratification MAE: {:.3f}+-{:.3f}'.format(means, stds))

means, stds = np.mean(ps_matching, axis=0), sem(ps_matching, axis=0)
print('Matching MAE: {:.3f}+-{:.3f}'.format(means, stds))

means, stds = np.mean(linear_mae, axis=0), sem(linear_mae, axis=0)
print('Linear MAE: {:.3f}+-{:.3f}'.format(means, stds))

means, stds = np.mean(z_estimator_mae, axis=0), sem(z_estimator_mae, axis=0)
print('Z-estimator MAE: {:.3f}+-{:.3f}'.format(means, stds))

Weighting MAE: 1.661+-0.046
Matching MAE: 0.202+-0.008
Linear MAE: 0.726+-0.038
Z-estimator MAE: 9.288+-0.401
